# 单卡GPU 进行 ChatGLM3-6B模型 LORA 高效微调
本 Cookbook 将带领开发者使用 `AdvertiseGen` 对 ChatGLM3-6B 数据集进行 lora微调，使其具备专业的广告生成能力。

## 硬件需求
显存：24GB
显卡架构：安培架构（推荐）
内存：16GB

## 1. 准备数据集
我们使用 AdvertiseGen 数据集来进行微调。从 [Google Drive](https://drive.google.com/file/d/13_vf0xRTQsyneRKdD1bZIr93vBGOczrk/view?usp=sharing) 或者 [Tsinghua Cloud](https://cloud.tsinghua.edu.cn/f/b3f119a008264b1cabd1/?dl=1) 下载处理好的 AdvertiseGen 数据集，将解压后的 AdvertiseGen 目录放到本目录的 `/data/` 下, 例如。
> /media/zr/Data/Code/ChatGLM3/finetune_demo/data/AdvertiseGen

接着，运行本代码来切割数据集

In [1]:
import json
from typing import Union
from pathlib import Path


def _resolve_path(path: Union[str, Path]) -> Path:
    return Path(path).expanduser().resolve()


def _mkdir(dir_name: Union[str, Path]):
    dir_name = _resolve_path(dir_name)
    if not dir_name.is_dir():
        dir_name.mkdir(parents=True, exist_ok=False)


def convert_adgen(data_dir: Union[str, Path], save_dir: Union[str, Path]):
    def _convert(in_file: Path, out_file: Path):
        _mkdir(out_file.parent)
        with open(in_file, encoding='utf-8') as fin:
            with open(out_file, 'wt', encoding='utf-8') as fout:
                for line in fin:
                    dct = json.loads(line)
                    sample = {'conversations': [{'role': 'user', 'content': dct['content']},
                                                {'role': 'assistant', 'content': dct['summary']}]}
                    fout.write(json.dumps(sample, ensure_ascii=False) + '\n')

    data_dir = _resolve_path(data_dir)
    save_dir = _resolve_path(save_dir)

    train_file = data_dir / 'train.json'
    if train_file.is_file():
        out_file = save_dir / train_file.relative_to(data_dir)
        _convert(train_file, out_file)

    dev_file = data_dir / 'dev.json'
    if dev_file.is_file():
        out_file = save_dir / dev_file.relative_to(data_dir)
        _convert(dev_file, out_file)


convert_adgen('/root/data/AdvertiseGen', '/root/data/AdvertiseGen_fix')

## 2. 使用命令行开始微调,我们使用 lora 进行微调
接着，我们仅需要将配置好的参数以命令行的形式传参给程序，就可以使用命令行进行高效微调，这里将 `/media/zr/Data/Code/ChatGLM3/venv/bin/python3` 换成你的 python3 的绝对路径以保证正常运行。

In [2]:
!/root/miniconda3/envs/llm/bin/python finetune_hf.py  /root/data/AdvertiseGen_fix  /root/autodl-tmp/chatglm3-6b/  configs/lora.yaml

Setting eos_token is not supported, use the default one.
Setting pad_token is not supported, use the default one.
Setting unk_token is not supported, use the default one.



Loading checkpoint shards:   0%|                          | 0/7 [00:00<?, ?it/s]


Loading checkpoint shards:  14%|██▌               | 1/7 [00:00<00:02,  2.59it/s]


Loading checkpoint shards:  29%|█████▏            | 2/7 [00:00<00:01,  2.82it/s]


Loading checkpoint shards:  43%|███████▋          | 3/7 [00:01<00:01,  2.93it/s]

...


 96%|█████████████████████████████████████████  | 64/67 [02:24<00:06,  2.19s/it]


 97%|█████████████████████████████████████████▋ | 65/67 [02:26<00:03,  2.00s/it]


 99%|██████████████████████████████████████████▎| 66/67 [02:28<00:01,  1.97s/it]


100%|███████████████████████████████████████████| 67/67 [02:30<00:00,  1.98s/it]


100%|███████████████████████████████████████████| 67/67 [02:34<00:00,  2.31s/it]


## 3. 使用微调的数据集进行推理
在完成微调任务之后，我们可以查看到 `output` 文件夹下多了很多个`checkpoint-*`的文件夹，这些文件夹代表了训练的轮数。
我们选择最后一轮的微调权重，并使用inference进行导入。

In [3]:
!ls output/

checkpoint-10000  checkpoint-25000  checkpoint-40000  checkpoint-50000
checkpoint-15000  checkpoint-30000  checkpoint-45000
checkpoint-20000  checkpoint-35000  checkpoint-5000


In [2]:
!CUDA_VISIBLE_DEVICES=1  /root/miniconda3/envs/llm/bin/python inference_hf.py output/checkpoint-50000/ --prompt "类型#裙*版型#显瘦*材质#网纱*风格#性感*裙型#百褶*裙下摆#压褶*裙长#连衣裙*裙衣门襟#拉链*裙衣门襟#套头*裙款式#拼接*裙款式#拉链*裙款式#木耳边*裙款式#抽褶*裙款式#不规则"

Loading checkpoint shards: 100%|██████████████████| 7/7 [00:00<00:00, 15.00it/s]
Setting eos_token is not supported, use the default one.
Setting pad_token is not supported, use the default one.
Setting unk_token is not supported, use the default one.
这款连衣裙采用拼接木耳边设计，优雅中不失性感，不规则的裙摆，增加裙子的时尚感。袖口和裙摆采用网纱压褶设计，穿着更加有层次感。拼接的百褶裙摆，穿着更加显瘦，套头的设计，穿脱方便，腰间有拉链设计，穿着更加方便 Roland<UNK>。


In [1]:
!CUDA_VISIBLE_DEVICES=1  /root/miniconda3/envs/llm/bin/python inference_hf.py output/checkpoint-10000/ --prompt "类型#裙*版型#显瘦*材质#网纱*风格#性感*裙型#百褶*裙下摆#压褶*裙长#连衣裙*裙衣门襟#拉链*裙衣门襟#套头*裙款式#拼接*裙款式#拉链*裙款式#木耳边*裙款式#抽褶*裙款式#不规则"

Loading checkpoint shards: 100%|██████████████████| 7/7 [00:00<00:00, 12.56it/s]
Setting eos_token is not supported, use the default one.
Setting pad_token is not supported, use the default one.
Setting unk_token is not supported, use the default one.
这款连衣裙，网纱拼接设计，穿着舒适，舒适度好。不规则的百褶裙摆，增添几分灵动感。加上抽褶的百褶，轻松遮肉显瘦，轻松穿出纤细的腰肢。拼接的木耳边，增加整体层次感。而压褶的百褶裙摆，更添几分俏皮感。加上门襟的拉链，穿着方便，穿着舒适。


## 4. 总结
到此位置，我们就完成了使用单张 GPU Lora 来微调 ChatGLM3-6B 模型，使其能生产出更好的广告。
在本章节中，你将会学会：
+ 如何使用模型进行 Lora 微调
+ 微调数据集的准备和对齐
+ 使用微调的模型进行推理